In [1]:
#pip install torch

In [2]:
# PyTorch
import torch
import torch.nn as nn
from torch.utils.data import Dataset, DataLoader
from sklearn.model_selection import train_test_split, StratifiedShuffleSplit
from sklearn.preprocessing import StandardScaler

# For data preprocess
import numpy as np
import pandas as pd
import csv
import os

# For plotting
import matplotlib.pyplot as plt
from matplotlib.pyplot import figure

from random import randrange, random, randint
import time

myseed = 42069  # set a random seed for reproducibility
torch.backends.cudnn.deterministic = True
torch.backends.cudnn.benchmark = False
np.random.seed(myseed)
torch.manual_seed(myseed)
if torch.cuda.is_available():
    torch.cuda.manual_seed_all(myseed)

# 1.Boston Dataset Analysis

## 1.1 MLP

In [3]:
df = pd.read_csv('Boston.csv')
df = df[df['crim'] < 20]
#df = pd.read_csv('covid.train.csv')

In [4]:
torch.cuda.is_available()

False

In [5]:
class NeuralNet(nn.Module):
    ''' 
    A fully-connected neural network
    '''
    
    def __init__(self, input_dim):
        super(NeuralNet, self).__init__()

        # Define your neural network here
        # TODO: How to modify this model to achieve better performance?
        self.net = nn.Sequential(
            nn.Linear(input_dim, 100),
            nn.ReLU(),
            nn.Linear(100, 1)
        )

        # Mean squared error loss
        self.criterion = nn.MSELoss(reduction='mean')

    def forward(self, x):
        ''' Given input of size (batch_size x input_dim), compute output of the network '''
        return self.net(x).squeeze(1)

    def cal_loss(self, pred, target, alpha=0, L1_w=0):
        ''' Calculate loss '''
        
        # Regularization
        # L0 is no regularization, L1 is L1 regularization L2 is regularization.
        L1_term = 0
        L2_term = 0
        
        if alpha != 0:
            for name, w in self.net.named_parameters():
                if 'weight' in name:
                    L1_term += alpha * torch.norm(w, p = 1).to(device)  # lasso
                    L2_term += alpha * torch.norm(w, p = 2).to(device)  # ridge

        return self.criterion(pred, target) + alpha * ((1-L1_w) * L2_term + L1_w * L1_term)

In [6]:
class BostonDataset(Dataset):
    
    def __init__(self, df, mode='train', random_state=0):
        self.mode = mode
        scalar = StandardScaler()
        df = scalar.fit_transform(df)
        df = pd.DataFrame(df)
        target = df.iloc[:,0]
        data = df.iloc[:, 1:]
        
        # Generation the indices of traning data and testing data
        indices_train, indices_test = train_test_split([i for i in range(data.shape[0])], test_size = 0.2, random_state = random_state)
        
        if mode == 'train':
            indices = indices_train
        elif mode == 'test':
            indices = indices_test
            
        data = data.to_numpy()
        target = target.to_numpy()
        self.data = torch.FloatTensor(data[indices])
        self.target = torch.FloatTensor(target[indices])
        self.dim = self.data.shape[1]

        # Normlization
        # self.data = (self.data- self.data.mean(dim=0, keepdim=True)) / self.data.std(dim=0, keepdim=True)

        print('Finish reading the {} data. {}samples and dim = {}'.format(self.mode, len(self.data), self.dim))
        
    def __getitem__(self, index):
        return self.data[index], self.target[index]
    
    def __len__(self):
        return len(self.data)


In [7]:
# data loader

def data_loader(df, mode, batch_size, n_jobs=0, random_state=0):
    dataset = BostonDataset(df, mode=mode,random_state=random_state)
    dataloader = DataLoader(dataset, batch_size, 
                            shuffle=(mode == 'train'), 
                            drop_last=False,
                            num_workers=n_jobs, pin_memory=True)
    
    return dataloader

In [8]:
def train(train_data, test_data, model, config, device):
    n_epochs = config['n_epochs']
    
    optimizer = getattr(torch.optim, config['optimizer'])(
        model.parameters(), **config['optim_hparas'])
    
    min_loss = float('1000.')
    
    loss_record = {'train':[], 'test': []}
    
    cnt_no_improvement = 0
    
    epoch = 0
    
    while epoch  < n_epochs:
        model.train()
        for x, y in train_data:
            optimizer.zero_grad()
            x, y = x.to(device), y.to(device)
            y_hat = model(x)
            loss = model.cal_loss(y_hat, y, alpha=config['alpha'], L1_w=config['L1_w'])
            loss.backward()
            optimizer.step()
            loss_record['train'].append(loss.detach().cpu().item())
        
        test_loss,_ = test(test_data, model, config, device)
        
        if test_loss < min_loss:
            min_loss = test_loss
            print('epoch {}, loss {:.6f}'.format(epoch + 1, min_loss))
            cnt_no_improvement = 0
        else:
            cnt_no_improvement += 1
            
        epoch += 1
        loss_record['test'].append(test_loss)
            

        if cnt_no_improvement > config['early_stop']:
            break
    
    print('Final loss is {:.6f} after {} epochs'.format(min_loss, epoch))

    return min_loss, loss_record

In [9]:
def test(data, model, config, device):
    model.eval()
    total_loss = 0
    for x, y in data:
        x, y = x.to(device), y.to(device)
        with torch.no_grad():
            y_hat = model(x)
            loss = model.cal_loss(y_hat, y, alpha=config['alpha'], L1_w=config['L1_w'])
        total_loss += loss.detach().cpu().item() * len(x)
    total_loss = total_loss / len(data.dataset)
    return total_loss, y_hat

In [10]:
def get_device():
    ''' Get device (if GPU is available, use GPU) '''
    return 'cuda' if torch.cuda.is_available() else 'cpu'

device = get_device()                 # get the current available device ('cpu' or 'cuda')
os.makedirs('models', exist_ok=True)  # The trained model will be saved to ./models/

# TODO: How to tune these hyper-parameters to improve your model's performance?
config = {
    'n_epochs': 1000,                # maximum number of epochs
    'batch_size': 98,               # mini-batch size for dataloader
    'optimizer': 'SGD',              # optimization algorithm (optimizer in torch.optim)
    'optim_hparas': {                # hyper-parameters for the optimizer (depends on which optimizer you are using)
        'lr': 0.001,                 # learning rate of SGD
        'momentum': 0.8             # momentum for SGD
    },
    'early_stop': 200,               # early stopping epochs (the number epochs since your model's last improvement)
    'save_path': 'models/model.pth', # your model will be saved here
    'L1_w': 0,                       # weight of L1 term
    'alpha': 0                       # weight of regularizaition terms
}

In [11]:
# delete maybe
train_data = data_loader(df, 'train', config['batch_size'])
test_data = data_loader(df, 'test', config['batch_size'])
model = NeuralNet(train_data.dataset.dim) # Construct model and move to device
model_loss, model_loss_record = train(train_data, test_data, model, config, device)

Finish reading the train data. 390samples and dim = 13
Finish reading the test data. 98samples and dim = 13
epoch 1, loss 0.706963
epoch 2, loss 0.555873
epoch 3, loss 0.442656
epoch 4, loss 0.364305
epoch 5, loss 0.314125
epoch 6, loss 0.282563
epoch 7, loss 0.261891
epoch 8, loss 0.247201
epoch 9, loss 0.236597
epoch 10, loss 0.228045
epoch 11, loss 0.220753
epoch 12, loss 0.214037
epoch 13, loss 0.208758
epoch 14, loss 0.203318
epoch 15, loss 0.198954
epoch 16, loss 0.194620
epoch 17, loss 0.190556
epoch 18, loss 0.187277
epoch 19, loss 0.183404
epoch 20, loss 0.180150
epoch 21, loss 0.177313
epoch 22, loss 0.174804
epoch 23, loss 0.172250
epoch 24, loss 0.169425
epoch 25, loss 0.167572
epoch 26, loss 0.165450
epoch 27, loss 0.163450
epoch 28, loss 0.161660
epoch 29, loss 0.159989
epoch 30, loss 0.158537
epoch 31, loss 0.156948
epoch 32, loss 0.155686
epoch 33, loss 0.153989
epoch 34, loss 0.152576
epoch 35, loss 0.151278
epoch 36, loss 0.150470
epoch 37, loss 0.149501
epoch 38, los

epoch 653, loss 0.102292
epoch 654, loss 0.102193
epoch 657, loss 0.102163
epoch 664, loss 0.101990
epoch 674, loss 0.101833
epoch 678, loss 0.101791
epoch 685, loss 0.101732
epoch 686, loss 0.101689
epoch 687, loss 0.101666
epoch 690, loss 0.101610
epoch 691, loss 0.101558
epoch 697, loss 0.101542
epoch 698, loss 0.101438
epoch 706, loss 0.101415
epoch 709, loss 0.101408
epoch 710, loss 0.101228
epoch 711, loss 0.101209
epoch 714, loss 0.101064
epoch 721, loss 0.100989
epoch 727, loss 0.100937
epoch 728, loss 0.100855
epoch 729, loss 0.100820
epoch 736, loss 0.100788
epoch 737, loss 0.100651
epoch 739, loss 0.100592
epoch 744, loss 0.100555
epoch 745, loss 0.100522
epoch 752, loss 0.100446
epoch 757, loss 0.100313
epoch 767, loss 0.100225
epoch 769, loss 0.100119
epoch 770, loss 0.100052
epoch 786, loss 0.100033
epoch 788, loss 0.100012
epoch 790, loss 0.099817
epoch 801, loss 0.099800
epoch 802, loss 0.099793
epoch 806, loss 0.099710
epoch 809, loss 0.099633
epoch 816, loss 0.099488


In [12]:
def plot_learning_curve(loss_record, title=''):
    ''' Plot learning curve of your DNN (train & dev loss) '''
    total_steps = len(loss_record['train'])
    x_1 = range(total_steps)
    x_2 = x_1[::len(loss_record['train']) // len(loss_record['test'])]
    figure(figsize=(8, 6))
    plt.plot(x_1, loss_record['train'], c='tab:red', label='train')
    plt.plot(x_2, loss_record['test'], c='tab:cyan', label='test')
    plt.ylim(0.0, 2)
    plt.xlabel('Training steps')
    plt.ylabel('MSE loss')
    plt.title('Learning curve of {}'.format(title))
    plt.legend()
    plt.show()

In [13]:
plot_learning_curve(model_loss_record, title='deep model')

In [14]:
# 5 fold validation
config_default = {
    'n_epochs': 1000,                # maximum number of epochs
    'batch_size': 98,               # mini-batch size for dataloader
    'optimizer': 'SGD',              # optimization algorithm (optimizer in torch.optim)
    'optim_hparas': {                # hyper-parameters for the optimizer (depends on which optimizer you are using)
        'lr': 0.001,                 # learning rate of SGD
        'momentum': 0.8             # momentum for SGD
    },
    'early_stop': 200,               # early stopping epochs (the number epochs since your model's last improvement)
    'save_path': 'models/model.pth', # your model will be saved here
    'L1_w': 0,                       # weight of L1 term
    'alpha': 0                       # weight of regularizaition terms
}

loss_record_5_fold = []
for j in range(5):
    train_data = data_loader(df, 'train', config['batch_size'],random_state=j)
    test_data = data_loader(df, 'test', config['batch_size'],random_state=j)
    model = NeuralNet(train_data.dataset.dim)

    model_loss, _ = train(train_data, test_data, model, config_default, device)

    loss_record_5_fold.append(model_loss)

mean_loss = np.mean(loss_record_5_fold)
std_loss = np.std(loss_record_5_fold)
print('The mean loss is {}\nSTD is {}'.format(mean_loss, std_loss))

Finish reading the train data. 390samples and dim = 13
Finish reading the test data. 98samples and dim = 13
epoch 1, loss 0.617600
epoch 2, loss 0.527079
epoch 3, loss 0.444674
epoch 4, loss 0.380461
epoch 5, loss 0.332362
epoch 6, loss 0.296625
epoch 7, loss 0.269107
epoch 8, loss 0.247704
epoch 9, loss 0.230956
epoch 10, loss 0.217791
epoch 11, loss 0.207168
epoch 12, loss 0.198261
epoch 13, loss 0.190994
epoch 14, loss 0.184721
epoch 15, loss 0.179341
epoch 16, loss 0.174898
epoch 17, loss 0.170852
epoch 18, loss 0.167611
epoch 19, loss 0.164172
epoch 20, loss 0.160934
epoch 21, loss 0.158594
epoch 22, loss 0.156319
epoch 23, loss 0.154207
epoch 24, loss 0.152780
epoch 25, loss 0.150399
epoch 26, loss 0.148415
epoch 27, loss 0.147039
epoch 28, loss 0.145808
epoch 29, loss 0.144073
epoch 30, loss 0.143207
epoch 31, loss 0.142247
epoch 32, loss 0.141330
epoch 33, loss 0.140293
epoch 34, loss 0.139328
epoch 35, loss 0.138483
epoch 36, loss 0.137803
epoch 37, loss 0.137448
epoch 38, los

epoch 618, loss 0.099668
epoch 620, loss 0.099644
epoch 621, loss 0.099608
epoch 623, loss 0.099567
epoch 627, loss 0.099565
epoch 628, loss 0.099277
epoch 631, loss 0.099249
epoch 632, loss 0.099156
epoch 633, loss 0.099144
epoch 635, loss 0.099101
epoch 641, loss 0.099052
epoch 645, loss 0.098993
epoch 652, loss 0.098969
epoch 653, loss 0.098893
epoch 654, loss 0.098872
epoch 655, loss 0.098759
epoch 660, loss 0.098648
epoch 663, loss 0.098601
epoch 666, loss 0.098582
epoch 668, loss 0.098530
epoch 670, loss 0.098504
epoch 672, loss 0.098389
epoch 675, loss 0.098364
epoch 677, loss 0.098292
epoch 683, loss 0.098255
epoch 684, loss 0.098229
epoch 685, loss 0.098218
epoch 686, loss 0.098114
epoch 687, loss 0.098076
epoch 688, loss 0.098072
epoch 689, loss 0.098025
epoch 700, loss 0.097924
epoch 702, loss 0.097895
epoch 703, loss 0.097794
epoch 710, loss 0.097766
epoch 712, loss 0.097670
epoch 713, loss 0.097566
epoch 718, loss 0.097499
epoch 723, loss 0.097483
epoch 724, loss 0.097314


epoch 592, loss 0.208220
epoch 594, loss 0.208203
epoch 595, loss 0.208187
epoch 600, loss 0.207898
epoch 605, loss 0.207831
epoch 606, loss 0.207668
epoch 608, loss 0.207472
epoch 610, loss 0.207326
epoch 617, loss 0.207260
epoch 620, loss 0.207165
epoch 622, loss 0.206929
epoch 625, loss 0.206681
epoch 635, loss 0.206544
epoch 636, loss 0.206531
epoch 642, loss 0.206275
epoch 643, loss 0.206100
epoch 650, loss 0.205990
epoch 658, loss 0.205837
epoch 660, loss 0.205691
epoch 661, loss 0.205637
epoch 669, loss 0.205005
epoch 681, loss 0.204514
epoch 691, loss 0.204316
epoch 704, loss 0.204002
epoch 720, loss 0.203944
epoch 725, loss 0.203838
epoch 730, loss 0.203826
epoch 734, loss 0.203568
epoch 738, loss 0.203521
epoch 746, loss 0.203017
epoch 751, loss 0.202994
epoch 758, loss 0.202749
epoch 767, loss 0.201904
epoch 793, loss 0.201711
epoch 806, loss 0.201619
epoch 813, loss 0.201476
epoch 817, loss 0.201282
epoch 818, loss 0.200772
epoch 821, loss 0.200704
epoch 835, loss 0.200698


epoch 643, loss 0.283477
epoch 646, loss 0.283268
epoch 656, loss 0.282664
epoch 668, loss 0.282405
epoch 689, loss 0.282012
epoch 696, loss 0.282005
epoch 697, loss 0.281889
epoch 698, loss 0.281730
epoch 714, loss 0.281725
epoch 717, loss 0.281440
epoch 720, loss 0.281379
epoch 727, loss 0.281123
epoch 736, loss 0.280834
epoch 747, loss 0.280817
epoch 754, loss 0.280063
epoch 782, loss 0.280063
epoch 784, loss 0.280048
epoch 787, loss 0.279788
epoch 807, loss 0.279525
epoch 808, loss 0.279437
epoch 809, loss 0.279298
epoch 817, loss 0.279022
epoch 821, loss 0.279020
epoch 834, loss 0.278772
epoch 835, loss 0.278606
epoch 846, loss 0.278401
epoch 854, loss 0.278296
epoch 870, loss 0.278290
epoch 875, loss 0.278248
epoch 883, loss 0.278239
epoch 885, loss 0.277610
epoch 894, loss 0.277340
epoch 923, loss 0.277073
epoch 938, loss 0.276902
epoch 965, loss 0.276733
epoch 983, loss 0.276495
Final loss is 0.276495 after 1000 epochs
Finish reading the train data. 390samples and dim = 13
Fini

epoch 373, loss 0.197817
epoch 374, loss 0.197640
epoch 375, loss 0.197484
epoch 377, loss 0.197312
epoch 380, loss 0.197077
epoch 381, loss 0.196829
epoch 385, loss 0.196785
epoch 389, loss 0.196502
epoch 390, loss 0.196462
epoch 392, loss 0.196400
epoch 393, loss 0.196156
epoch 397, loss 0.196118
epoch 398, loss 0.196090
epoch 399, loss 0.195616
epoch 401, loss 0.195573
epoch 407, loss 0.195202
epoch 413, loss 0.194858
epoch 419, loss 0.194523
epoch 420, loss 0.194427
epoch 426, loss 0.194211
epoch 429, loss 0.194185
epoch 430, loss 0.194102
epoch 435, loss 0.193810
epoch 440, loss 0.193630
epoch 441, loss 0.193610
epoch 442, loss 0.193565
epoch 443, loss 0.193223
epoch 449, loss 0.193060
epoch 450, loss 0.193001
epoch 455, loss 0.192886
epoch 461, loss 0.192798
epoch 463, loss 0.192470
epoch 465, loss 0.192463
epoch 466, loss 0.192324
epoch 474, loss 0.192068
epoch 482, loss 0.191691
epoch 487, loss 0.191660
epoch 491, loss 0.191562
epoch 496, loss 0.191444
epoch 502, loss 0.191034


epoch 306, loss 0.208724
epoch 309, loss 0.208544
epoch 310, loss 0.208468
epoch 311, loss 0.208316
epoch 316, loss 0.208117
epoch 318, loss 0.207691
epoch 319, loss 0.207560
epoch 326, loss 0.207358
epoch 330, loss 0.207060
epoch 331, loss 0.207042
epoch 332, loss 0.207009
epoch 334, loss 0.206909
epoch 336, loss 0.206830
epoch 338, loss 0.206710
epoch 339, loss 0.206633
epoch 340, loss 0.206614
epoch 343, loss 0.206336
epoch 344, loss 0.206211
epoch 349, loss 0.205763
epoch 352, loss 0.205500
epoch 357, loss 0.205441
epoch 362, loss 0.205347
epoch 365, loss 0.205215
epoch 366, loss 0.204872
epoch 367, loss 0.204857
epoch 372, loss 0.204736
epoch 374, loss 0.204731
epoch 376, loss 0.204693
epoch 377, loss 0.204449
epoch 378, loss 0.204413
epoch 379, loss 0.204218
epoch 382, loss 0.204209
epoch 385, loss 0.204202
epoch 390, loss 0.203948
epoch 391, loss 0.203719
epoch 392, loss 0.203630
epoch 396, loss 0.203390
epoch 402, loss 0.203285
epoch 403, loss 0.203196
epoch 408, loss 0.202819


In [15]:
loss_record_5_fold

[0.09356441348791122,
 0.19682064652442932,
 0.27649474143981934,
 0.18412576615810394,
 0.1920863538980484]

## 1.2 MLP with L1 regularization

In [19]:
# Tune hyperparameters with 5 folds validation
# Tune alpha only

config_random_L1 = {
    'n_epochs': 1000,                # maximum number of epochs
    'batch_size': 98,                # mini-batch size for dataloader
    'optimizer': 'SGD',              # optimization algorithm (optimizer in torch.optim)
    'optim_hparas': {                # hyper-parameters for the optimizer (depends on which optimizer you are using)
        'lr': 0.001,                 # learning rate of SGD
        'momentum': 0.8              # momentum for SGD
    },
    'early_stop': 200,               # early stopping epochs (the number epochs since your model's last improvement)
    'save_path': 'models/model.pth', # your model will be saved here
    'L1_w': 1,      # weight of L1 term
    'alpha': [1, .1, .3, .5, .7, .9, .01, .03, .05, .07, .09, .001, .003, .005, .007, .009, .0001, .0003, .0005, .0007, .0009]  # weight of regularizaition terms
}

def random_search_L1(iteration, config_random):
    print('test')
    iteration = iteration
    min_loss = 1000
    config_best = None
    
    config_record = []
    for i in range(iteration):
        config_candidate = config_random.copy()
        alpha_index = randint(0,len(config_candidate['alpha'])-1)
        
        if alpha_index in config_record:  # if a config has been tested then skip it
            continue
        
        config_record.append(alpha_index)
        
        loss_record_5_fold = []
        
        config_candidate['alpha'] = config_candidate['alpha'][alpha_index]
        
        # 5 fold validation
        for j in range(5):
            train_data_L1 = data_loader(df, 'train', config_candidate['batch_size'], random_state=j)
            test_data_L1 = data_loader(df, 'test', config_candidate['batch_size'], random_state=j)
            model_L1 = NeuralNet(train_data_L1.dataset.dim)

            model_loss_L1, model_loss_record_L1 = train(train_data_L1, test_data_L1, model_L1, config_candidate, device)
            
            loss_record_5_fold.append(model_loss_L1)
        
        mean_loss = np.mean(loss_record_5_fold)
        
        if mean_loss < min_loss:
            min_loss = mean_loss
            config_best = config_candidate
    print('The lowest loss is {}\nConfig is {}'.format(min_loss, config_best))

time_start = time.time()
random_search_L1(50, config_random_L1)
time_end = time.time()
print('Total Time: ', time_end-time_start)

test
Finish reading the train data. 390samples and dim = 13
Finish reading the test data. 98samples and dim = 13
epoch 1, loss 0.868011
epoch 2, loss 0.745865
epoch 3, loss 0.628899
epoch 4, loss 0.536468
epoch 5, loss 0.468964
epoch 6, loss 0.419895
epoch 7, loss 0.381298
epoch 8, loss 0.352442
epoch 9, loss 0.328693
epoch 10, loss 0.308354
epoch 11, loss 0.291339
epoch 12, loss 0.276150
epoch 13, loss 0.262548
epoch 14, loss 0.249850
epoch 15, loss 0.238449
epoch 16, loss 0.228464
epoch 17, loss 0.219106
epoch 18, loss 0.210766
epoch 19, loss 0.202352
epoch 20, loss 0.195806
epoch 21, loss 0.188847
epoch 22, loss 0.182770
epoch 23, loss 0.177160
epoch 24, loss 0.172186
epoch 25, loss 0.166987
epoch 26, loss 0.162860
epoch 27, loss 0.159749
epoch 28, loss 0.155904
epoch 29, loss 0.152695
epoch 30, loss 0.149975
epoch 31, loss 0.147311
epoch 32, loss 0.145100
epoch 33, loss 0.142906
epoch 34, loss 0.140714
epoch 35, loss 0.138669
epoch 36, loss 0.136980
epoch 37, loss 0.134821
epoch 38

epoch 811, loss 0.097995
epoch 813, loss 0.097956
epoch 816, loss 0.097951
epoch 817, loss 0.097942
epoch 818, loss 0.097932
epoch 821, loss 0.097920
epoch 824, loss 0.097867
epoch 825, loss 0.097824
epoch 826, loss 0.097684
epoch 831, loss 0.097683
epoch 832, loss 0.097676
epoch 834, loss 0.097662
epoch 837, loss 0.097587
epoch 838, loss 0.097545
epoch 839, loss 0.097530
epoch 840, loss 0.097414
epoch 845, loss 0.097334
epoch 846, loss 0.097266
epoch 854, loss 0.097213
epoch 856, loss 0.097191
epoch 857, loss 0.097128
epoch 858, loss 0.097115
epoch 859, loss 0.096953
epoch 866, loss 0.096867
epoch 868, loss 0.096802
epoch 870, loss 0.096792
epoch 872, loss 0.096767
epoch 873, loss 0.096747
epoch 876, loss 0.096707
epoch 880, loss 0.096626
epoch 881, loss 0.096522
epoch 887, loss 0.096460
epoch 893, loss 0.096440
epoch 894, loss 0.096373
epoch 895, loss 0.096312
epoch 899, loss 0.096108
epoch 900, loss 0.096012
epoch 916, loss 0.095894
epoch 918, loss 0.095850
epoch 923, loss 0.095839


epoch 69, loss 0.323294
epoch 70, loss 0.322058
epoch 71, loss 0.321870
epoch 72, loss 0.321776
epoch 73, loss 0.320836
epoch 74, loss 0.319971
epoch 75, loss 0.319380
epoch 76, loss 0.319067
epoch 77, loss 0.318737
epoch 78, loss 0.318575
epoch 79, loss 0.317412
epoch 80, loss 0.317305
epoch 82, loss 0.316763
epoch 83, loss 0.315954
epoch 84, loss 0.315070
epoch 85, loss 0.314332
epoch 87, loss 0.313628
epoch 88, loss 0.313146
epoch 89, loss 0.312775
epoch 90, loss 0.312744
epoch 91, loss 0.312615
epoch 92, loss 0.312435
epoch 93, loss 0.311329
epoch 94, loss 0.311182
epoch 95, loss 0.310913
epoch 96, loss 0.310759
epoch 97, loss 0.310624
epoch 98, loss 0.310165
epoch 99, loss 0.309368
epoch 100, loss 0.308771
epoch 101, loss 0.308639
epoch 102, loss 0.308062
epoch 104, loss 0.307636
epoch 108, loss 0.306792
epoch 109, loss 0.306023
epoch 113, loss 0.305807
epoch 114, loss 0.305795
epoch 115, loss 0.304928
epoch 119, loss 0.303778
epoch 121, loss 0.303720
epoch 122, loss 0.303090
epoc

epoch 230, loss 0.212089
epoch 231, loss 0.212084
epoch 232, loss 0.211989
epoch 235, loss 0.211742
epoch 236, loss 0.211518
epoch 239, loss 0.210831
epoch 245, loss 0.210572
epoch 246, loss 0.210253
epoch 248, loss 0.210076
epoch 249, loss 0.209900
epoch 253, loss 0.209776
epoch 255, loss 0.209536
epoch 258, loss 0.209233
epoch 259, loss 0.208965
epoch 260, loss 0.208681
epoch 264, loss 0.208670
epoch 266, loss 0.208655
epoch 267, loss 0.208395
epoch 268, loss 0.208314
epoch 269, loss 0.208239
epoch 270, loss 0.208158
epoch 271, loss 0.207904
epoch 274, loss 0.207823
epoch 275, loss 0.207721
epoch 276, loss 0.207627
epoch 277, loss 0.207601
epoch 278, loss 0.207292
epoch 279, loss 0.207195
epoch 280, loss 0.207125
epoch 284, loss 0.206937
epoch 285, loss 0.206617
epoch 288, loss 0.206530
epoch 289, loss 0.206421
epoch 290, loss 0.206326
epoch 291, loss 0.206220
epoch 294, loss 0.205978
epoch 295, loss 0.205614
epoch 298, loss 0.205609
epoch 299, loss 0.205586
epoch 300, loss 0.205411


epoch 257, loss 0.196765
epoch 260, loss 0.196442
epoch 261, loss 0.196289
epoch 264, loss 0.195797
epoch 270, loss 0.195744
epoch 271, loss 0.195365
epoch 275, loss 0.195343
epoch 279, loss 0.195121
epoch 280, loss 0.194906
epoch 283, loss 0.194492
epoch 287, loss 0.194470
epoch 288, loss 0.194108
epoch 290, loss 0.194037
epoch 291, loss 0.193996
epoch 295, loss 0.193942
epoch 296, loss 0.193933
epoch 300, loss 0.193602
epoch 304, loss 0.193376
epoch 306, loss 0.193202
epoch 307, loss 0.193139
epoch 310, loss 0.192657
epoch 317, loss 0.192568
epoch 318, loss 0.192485
epoch 319, loss 0.192187
epoch 323, loss 0.192149
epoch 331, loss 0.192031
epoch 332, loss 0.191816
epoch 335, loss 0.191605
epoch 338, loss 0.191511
epoch 339, loss 0.191335
epoch 343, loss 0.191334
epoch 344, loss 0.191174
epoch 345, loss 0.190859
epoch 346, loss 0.190815
epoch 347, loss 0.190636
epoch 357, loss 0.190593
epoch 361, loss 0.190521
epoch 362, loss 0.190183
epoch 367, loss 0.189999
epoch 376, loss 0.189973


...

epoch 131, loss 0.701132
epoch 132, loss 0.700771
epoch 133, loss 0.700339
epoch 134, loss 0.700034
epoch 135, loss 0.699650
epoch 136, loss 0.698978
epoch 137, loss 0.698739
epoch 138, loss 0.698095
epoch 139, loss 0.697634
epoch 140, loss 0.697321
epoch 141, loss 0.697008
epoch 142, loss 0.696539
epoch 143, loss 0.696212
epoch 144, loss 0.695743
epoch 145, loss 0.695329
epoch 146, loss 0.694709
epoch 147, loss 0.694420
epoch 148, loss 0.693801
epoch 149, loss 0.693623
epoch 150, loss 0.693529
epoch 151, loss 0.692974
epoch 152, loss 0.692563
epoch 153, loss 0.692203
epoch 154, loss 0.691576
epoch 155, loss 0.691357
epoch 156, loss 0.690719
epoch 157, loss 0.690329
epoch 158, loss 0.689907
epoch 159, loss 0.689641
epoch 160, loss 0.689403
epoch 161, loss 0.688905
epoch 162, loss 0.688452
epoch 163, loss 0.688206
epoch 164, loss 0.687952
epoch 165, loss 0.687468
epoch 166, loss 0.686998
epoch 167, loss 0.686511
epoch 168, loss 0.686364
epoch 169, loss 0.686008
epoch 170, loss 0.685622


epoch 515, loss 0.603751
epoch 516, loss 0.603469
epoch 517, loss 0.603413
epoch 518, loss 0.603393
epoch 519, loss 0.603219
epoch 520, loss 0.602805
epoch 521, loss 0.602651
epoch 522, loss 0.602509
epoch 523, loss 0.601991
epoch 524, loss 0.601752
epoch 526, loss 0.601635
epoch 527, loss 0.601236
epoch 531, loss 0.601019
epoch 532, loss 0.600751
epoch 534, loss 0.600703
epoch 536, loss 0.600223
epoch 537, loss 0.599895
epoch 538, loss 0.599874
epoch 539, loss 0.599432
epoch 541, loss 0.599405
epoch 542, loss 0.599240
epoch 543, loss 0.598882
epoch 544, loss 0.598512
epoch 545, loss 0.598222
epoch 547, loss 0.598215
epoch 550, loss 0.598055
epoch 551, loss 0.597817
epoch 552, loss 0.597432
epoch 553, loss 0.596988
epoch 554, loss 0.596831
epoch 555, loss 0.596771
epoch 556, loss 0.596740
epoch 557, loss 0.596561
epoch 558, loss 0.596503
epoch 559, loss 0.596353
epoch 560, loss 0.595966
epoch 562, loss 0.595837
epoch 563, loss 0.595638
epoch 564, loss 0.595435
epoch 565, loss 0.595203


epoch 987, loss 0.530047
epoch 988, loss 0.529331
epoch 991, loss 0.529128
epoch 992, loss 0.529078
epoch 993, loss 0.528823
epoch 994, loss 0.528592
epoch 997, loss 0.528528
epoch 999, loss 0.527882
epoch 1000, loss 0.527832
Final loss is 0.527832 after 1000 epochs
Finish reading the train data. 390samples and dim = 13
Finish reading the test data. 98samples and dim = 13
epoch 1, loss 1.512069
epoch 2, loss 1.360194
epoch 3, loss 1.221681
epoch 4, loss 1.117841
epoch 5, loss 1.042449
epoch 6, loss 0.989645
epoch 7, loss 0.953052
epoch 8, loss 0.925406
epoch 9, loss 0.905322
epoch 10, loss 0.889436
epoch 11, loss 0.876523
epoch 12, loss 0.865632
epoch 13, loss 0.855935
epoch 14, loss 0.847264
epoch 15, loss 0.839537
epoch 16, loss 0.832611
epoch 17, loss 0.826198
epoch 18, loss 0.820593
epoch 19, loss 0.815088
epoch 20, loss 0.810148
epoch 21, loss 0.805570
epoch 22, loss 0.801418
epoch 23, loss 0.797430
epoch 24, loss 0.793666
epoch 25, loss 0.790282
epoch 26, loss 0.787101
epoch 27, 

epoch 355, loss 0.632501
epoch 356, loss 0.632036
epoch 357, loss 0.631742
epoch 358, loss 0.631450
epoch 359, loss 0.631351
epoch 360, loss 0.631320
epoch 361, loss 0.631206
epoch 362, loss 0.630858
epoch 363, loss 0.630675
epoch 364, loss 0.630302
epoch 365, loss 0.630250
epoch 366, loss 0.629981
epoch 368, loss 0.629696
epoch 369, loss 0.629551
epoch 370, loss 0.629347
epoch 371, loss 0.628940
epoch 372, loss 0.628717
epoch 374, loss 0.628552
epoch 375, loss 0.628374
epoch 376, loss 0.628070
epoch 377, loss 0.627796
epoch 378, loss 0.627633
epoch 379, loss 0.627569
epoch 380, loss 0.627124
epoch 381, loss 0.626979
epoch 382, loss 0.626900
epoch 383, loss 0.626517
epoch 384, loss 0.626245
epoch 385, loss 0.626172
epoch 386, loss 0.626030
epoch 387, loss 0.625854
epoch 389, loss 0.625181
epoch 390, loss 0.625132
epoch 391, loss 0.625081
epoch 392, loss 0.624948
epoch 393, loss 0.624560
epoch 394, loss 0.624409
epoch 395, loss 0.623908
epoch 398, loss 0.623769
epoch 399, loss 0.623622


epoch 775, loss 0.560671
epoch 776, loss 0.560491
epoch 777, loss 0.560287
epoch 778, loss 0.559982
epoch 779, loss 0.559971
epoch 780, loss 0.559798
epoch 782, loss 0.559584
epoch 784, loss 0.559249
epoch 785, loss 0.559129
epoch 786, loss 0.559012
epoch 788, loss 0.558926
epoch 789, loss 0.558339
epoch 790, loss 0.558222
epoch 792, loss 0.558209
epoch 793, loss 0.557762
epoch 794, loss 0.557728
epoch 795, loss 0.557626
epoch 797, loss 0.557331
epoch 798, loss 0.557273
epoch 799, loss 0.557172
epoch 800, loss 0.557095
epoch 801, loss 0.556950
epoch 802, loss 0.556935
epoch 803, loss 0.556512
epoch 804, loss 0.556334
epoch 805, loss 0.556244
epoch 806, loss 0.556098
epoch 807, loss 0.555720
epoch 808, loss 0.555389
epoch 811, loss 0.555294
epoch 812, loss 0.555273
epoch 813, loss 0.555253
epoch 814, loss 0.554977
epoch 816, loss 0.554609
epoch 818, loss 0.554251
epoch 819, loss 0.553997
epoch 820, loss 0.553937
epoch 822, loss 0.553727
epoch 823, loss 0.553501
epoch 825, loss 0.553495


In [ ]:
###########################################

In [ ]:
config_l1 = {
    'n_epochs': 1000,                # maximum number of epochs
    'batch_size': 98,                # mini-batch size for dataloader
    'optimizer': 'SGD',              # optimization algorithm (optimizer in torch.optim)
    'optim_hparas': {                # hyper-parameters for the optimizer (depends on which optimizer you are using)
        'lr': 0.001,                 # learning rate of SGD
        'momentum': 0.8              # momentum for SGD
    },
    'early_stop': 200,               # early stopping epochs (the number epochs since your model's last improvement)
    'save_path': 'models/model.pth', # your model will be saved here
    'L1_w': 1,                       # weight of L1 term
    'alpha': 0.01                   # weight of regularizaition terms
}

In [ ]:
train_data_l1 = data_loader(df, 'train', config_l1['batch_size'])
test_data_l1 = data_loader(df, 'test', config_l1['batch_size'])
model_l1 = NeuralNet(train_data_l1.dataset.dim) # Construct model and move to device
model_loss_l1, model_loss_record_l1 = train(train_data_l1, test_data_l1, model_l1, config_l1, device)

In [ ]:
plot_learning_curve(model_loss_record_l1, title='Lasso')

## 1.3 MLP with L2 regularization

In [18]:
# Tune hyperparameters
# Tune allpha only

config_random_L2 = {
    'n_epochs': 1000,                # maximum number of epochs
    'batch_size': 98,                # mini-batch size for dataloader
    'optimizer': 'SGD',              # optimization algorithm (optimizer in torch.optim)
    'optim_hparas': {                # hyper-parameters for the optimizer (depends on which optimizer you are using)
        'lr': 0.001,                 # learning rate of SGD
        'momentum': 0.8              # momentum for SGD
    },
    'early_stop': 200,               # early stopping epochs (the number epochs since your model's last improvement)
    'save_path': 'models/model.pth', # your model will be saved here
    'L1_w': 0,      # weight of L1 term
    'alpha': [1, .1, .3, .5, .7, .9, .01, .03, .05, .07, .09, .001, .003, .005, .007, .009, .0001, .0003, .0005, .0007, .0009]  # weight of regularizaition terms
}

def random_search_L2(iteration, config_random):
    print('test')
    iteration = iteration
    min_loss = 1000
    config_best = None
    
    config_record = []
    
    for i in range(iteration):
        config_candidate = config_random.copy()
        alpha_index = randint(0,len(config_candidate['alpha'])-1)
        
        if alpha_index in config_record:  # if a config has been tested then skip it
            continue
        
        config_record.append(alpha_index)
        
        loss_record_5_fold = []
        
        config_candidate['alpha'] = config_candidate['alpha'][alpha_index]
        
        # 5 fold validation
        for j in range(5):
            train_data_L2 = data_loader(df, 'train', config_candidate['batch_size'], random_state=j)
            test_data_L2 = data_loader(df, 'test', config_candidate['batch_size'], random_state=j)
            model_L2 = NeuralNet(train_data_L2.dataset.dim)

            model_loss_L2, model_loss_record_L2 = train(train_data_L2, test_data_L2, model_L2, config_candidate, device)
            
            loss_record_5_fold.append(model_loss_L2)
        
        mean_loss = np.mean(loss_record_5_fold)
        
        if mean_loss < min_loss:
            min_loss = mean_loss
            config_best = config_candidate
            
    print('The lowest loss is {}\nConfig is {}'.format(min_loss, config_best))

time_start = time.time()
random_search_L2(50, config_random_L2)
time_end = time.time()
print('Total Time: ', time_end-time_start)

test
Finish reading the train data. 390samples and dim = 13
Finish reading the test data. 98samples and dim = 13
epoch 1, loss 0.834465
epoch 2, loss 0.685864
epoch 3, loss 0.555014
epoch 4, loss 0.470028
epoch 5, loss 0.413612
epoch 6, loss 0.375559
epoch 7, loss 0.346638
epoch 8, loss 0.325289
epoch 9, loss 0.308649
epoch 10, loss 0.294269
epoch 11, loss 0.282523
epoch 12, loss 0.272441
epoch 13, loss 0.263519
epoch 14, loss 0.255473
epoch 15, loss 0.248446
epoch 16, loss 0.241766
epoch 17, loss 0.235815
epoch 18, loss 0.229907
epoch 19, loss 0.224807
epoch 20, loss 0.220190
epoch 21, loss 0.215712
epoch 22, loss 0.211708
epoch 23, loss 0.208266
epoch 24, loss 0.204652
epoch 25, loss 0.200813
epoch 26, loss 0.197678
epoch 27, loss 0.195118
epoch 28, loss 0.192332
epoch 29, loss 0.189583
epoch 30, loss 0.187256
epoch 31, loss 0.185020
epoch 32, loss 0.182809
epoch 33, loss 0.180913
epoch 34, loss 0.179066
epoch 35, loss 0.177145
epoch 36, loss 0.175830
epoch 37, loss 0.173981
epoch 38

epoch 418, loss 0.099053
epoch 419, loss 0.098932
epoch 420, loss 0.098899
epoch 424, loss 0.098857
epoch 425, loss 0.098691
epoch 428, loss 0.098691
epoch 429, loss 0.098687
epoch 430, loss 0.098671
epoch 431, loss 0.098645
epoch 432, loss 0.098462
epoch 433, loss 0.098419
epoch 434, loss 0.098377
epoch 438, loss 0.098357
epoch 440, loss 0.098211
epoch 441, loss 0.098174
epoch 442, loss 0.098099
epoch 445, loss 0.098094
epoch 448, loss 0.097929
epoch 449, loss 0.097864
epoch 453, loss 0.097840
epoch 455, loss 0.097788
epoch 456, loss 0.097784
epoch 457, loss 0.097681
epoch 458, loss 0.097663
epoch 461, loss 0.097599
epoch 462, loss 0.097551
epoch 463, loss 0.097471
epoch 464, loss 0.097454
epoch 465, loss 0.097453
epoch 466, loss 0.097361
epoch 471, loss 0.097259
epoch 472, loss 0.097236
epoch 473, loss 0.097222
epoch 475, loss 0.097177
epoch 476, loss 0.097057
epoch 478, loss 0.096985
epoch 485, loss 0.096944
epoch 486, loss 0.096848
epoch 489, loss 0.096808
epoch 490, loss 0.096800


epoch 494, loss 0.188326
epoch 503, loss 0.187698
epoch 510, loss 0.187651
epoch 523, loss 0.187643
epoch 525, loss 0.187039
epoch 539, loss 0.186883
epoch 540, loss 0.186868
epoch 553, loss 0.186631
epoch 554, loss 0.186411
epoch 565, loss 0.185942
epoch 569, loss 0.185937
epoch 585, loss 0.185773
epoch 595, loss 0.185678
epoch 600, loss 0.185643
epoch 603, loss 0.185592
epoch 604, loss 0.185549
epoch 606, loss 0.184877
epoch 617, loss 0.184741
epoch 624, loss 0.184685
epoch 628, loss 0.184503
epoch 641, loss 0.184198
epoch 644, loss 0.183952
epoch 658, loss 0.183755
epoch 667, loss 0.183469
epoch 677, loss 0.183456
epoch 682, loss 0.183388
epoch 684, loss 0.183284
epoch 687, loss 0.183277
epoch 697, loss 0.182946
epoch 702, loss 0.182919
epoch 708, loss 0.182855
epoch 716, loss 0.182298
epoch 733, loss 0.182229
epoch 742, loss 0.182216
epoch 744, loss 0.182096
epoch 749, loss 0.181926
epoch 751, loss 0.181790
epoch 753, loss 0.181722
epoch 754, loss 0.181629
epoch 767, loss 0.181521


epoch 573, loss 0.281357
epoch 578, loss 0.280960
epoch 593, loss 0.280863
epoch 594, loss 0.280538
epoch 597, loss 0.280336
epoch 603, loss 0.280284
epoch 613, loss 0.279256
epoch 620, loss 0.279120
epoch 631, loss 0.279027
epoch 635, loss 0.278949
epoch 636, loss 0.278760
epoch 640, loss 0.278723
epoch 644, loss 0.278676
epoch 647, loss 0.278472
epoch 650, loss 0.278236
epoch 651, loss 0.277556
epoch 674, loss 0.276711
epoch 688, loss 0.276704
epoch 690, loss 0.276466
epoch 701, loss 0.276327
epoch 709, loss 0.276268
epoch 710, loss 0.276132
epoch 715, loss 0.275603
epoch 726, loss 0.275339
epoch 736, loss 0.274825
epoch 741, loss 0.274714
epoch 751, loss 0.274688
epoch 754, loss 0.274634
epoch 756, loss 0.274264
epoch 766, loss 0.274220
epoch 777, loss 0.273873
epoch 778, loss 0.273156
epoch 798, loss 0.272962
epoch 804, loss 0.272669
epoch 816, loss 0.272422
epoch 817, loss 0.271921
epoch 842, loss 0.271908
epoch 845, loss 0.271878
epoch 852, loss 0.271319
epoch 866, loss 0.271078


epoch 378, loss 0.208833
epoch 381, loss 0.208629
epoch 384, loss 0.208477
epoch 392, loss 0.208173
epoch 396, loss 0.208019
epoch 406, loss 0.207985
epoch 408, loss 0.207659
epoch 409, loss 0.207422
epoch 423, loss 0.207386
epoch 424, loss 0.207309
epoch 426, loss 0.207192
epoch 428, loss 0.207161
epoch 436, loss 0.206844
epoch 438, loss 0.206738
epoch 439, loss 0.206712
epoch 440, loss 0.206690
epoch 446, loss 0.206679
epoch 448, loss 0.206598
epoch 449, loss 0.206374
epoch 459, loss 0.206035
epoch 467, loss 0.205956
epoch 475, loss 0.205906
epoch 485, loss 0.205771
epoch 491, loss 0.205761
epoch 492, loss 0.205409
epoch 506, loss 0.205317
epoch 515, loss 0.205244
epoch 529, loss 0.205222
epoch 530, loss 0.205184
epoch 535, loss 0.205016
epoch 536, loss 0.205011
epoch 544, loss 0.204940
epoch 547, loss 0.204845
epoch 556, loss 0.204626
epoch 564, loss 0.204451
epoch 568, loss 0.204383
epoch 580, loss 0.204338
epoch 585, loss 0.204277
epoch 588, loss 0.204189
epoch 592, loss 0.204139


...

epoch 522, loss 0.139195
epoch 523, loss 0.139146
epoch 524, loss 0.139092
epoch 527, loss 0.138689
epoch 528, loss 0.138651
epoch 535, loss 0.138502
epoch 537, loss 0.138414
epoch 538, loss 0.138412
epoch 540, loss 0.138407
epoch 541, loss 0.138233
epoch 542, loss 0.138069
epoch 544, loss 0.138015
epoch 547, loss 0.137959
epoch 549, loss 0.137756
epoch 551, loss 0.137713
epoch 554, loss 0.137580
epoch 555, loss 0.137531
epoch 556, loss 0.137500
epoch 557, loss 0.137331
epoch 561, loss 0.137229
epoch 562, loss 0.137147
epoch 563, loss 0.137136
epoch 565, loss 0.137058
epoch 567, loss 0.136898
epoch 568, loss 0.136788
epoch 570, loss 0.136710
epoch 572, loss 0.136520
epoch 574, loss 0.136504
epoch 576, loss 0.136403
epoch 577, loss 0.136317
epoch 580, loss 0.136277
epoch 581, loss 0.136196
epoch 582, loss 0.136166
epoch 584, loss 0.136054
epoch 587, loss 0.136030
epoch 588, loss 0.135937
epoch 589, loss 0.135883
epoch 591, loss 0.135750
epoch 592, loss 0.135727
epoch 593, loss 0.135710


epoch 165, loss 0.237576
epoch 168, loss 0.237337
epoch 171, loss 0.237152
epoch 173, loss 0.236563
epoch 181, loss 0.236436
epoch 183, loss 0.236184
epoch 185, loss 0.236148
epoch 186, loss 0.235634
epoch 194, loss 0.235440
epoch 200, loss 0.235138
epoch 201, loss 0.234982
epoch 205, loss 0.234874
epoch 207, loss 0.234797
epoch 208, loss 0.234452
epoch 212, loss 0.234390
epoch 214, loss 0.233778
epoch 221, loss 0.233670
epoch 222, loss 0.233517
epoch 224, loss 0.233275
epoch 225, loss 0.232930
epoch 232, loss 0.232681
epoch 238, loss 0.232110
epoch 249, loss 0.232068
epoch 250, loss 0.231652
epoch 258, loss 0.231519
epoch 261, loss 0.231132
epoch 263, loss 0.231112
epoch 264, loss 0.230975
epoch 272, loss 0.230604
epoch 279, loss 0.230202
epoch 286, loss 0.229981
epoch 288, loss 0.229674
epoch 290, loss 0.229527
epoch 299, loss 0.229307
epoch 301, loss 0.229304
epoch 305, loss 0.229270
epoch 306, loss 0.229070
epoch 307, loss 0.228572
epoch 308, loss 0.228502
epoch 314, loss 0.228400


epoch 341, loss 0.320190
epoch 342, loss 0.319924
epoch 345, loss 0.319861
epoch 347, loss 0.319814
epoch 348, loss 0.319722
epoch 351, loss 0.319399
epoch 352, loss 0.319345
epoch 353, loss 0.319345
epoch 355, loss 0.319302
epoch 356, loss 0.318904
epoch 359, loss 0.318578
epoch 361, loss 0.318073
epoch 368, loss 0.317080
epoch 374, loss 0.316775
epoch 375, loss 0.316598
epoch 378, loss 0.316458
epoch 380, loss 0.316368
epoch 383, loss 0.315670
epoch 384, loss 0.315669
epoch 390, loss 0.315534
epoch 391, loss 0.315135
epoch 399, loss 0.314621
epoch 404, loss 0.314438
epoch 405, loss 0.314185
epoch 408, loss 0.313344
epoch 418, loss 0.313281
epoch 420, loss 0.312957
epoch 423, loss 0.312622
epoch 424, loss 0.312396
epoch 425, loss 0.312209
epoch 431, loss 0.312054
epoch 434, loss 0.311067
epoch 443, loss 0.310569
epoch 447, loss 0.310549
epoch 448, loss 0.310349
epoch 452, loss 0.310256
epoch 456, loss 0.309989
epoch 457, loss 0.309942
epoch 458, loss 0.309561
epoch 462, loss 0.309455


epoch 220, loss 0.251177
epoch 222, loss 0.250956
epoch 224, loss 0.250617
epoch 227, loss 0.250029
epoch 228, loss 0.249799
epoch 231, loss 0.249408
epoch 232, loss 0.249220
epoch 233, loss 0.248872
epoch 236, loss 0.248816
epoch 237, loss 0.248277
epoch 238, loss 0.248169
epoch 239, loss 0.247994
epoch 240, loss 0.247788
epoch 243, loss 0.247633
epoch 244, loss 0.247167
epoch 245, loss 0.246817
epoch 248, loss 0.246645
epoch 249, loss 0.246008
epoch 250, loss 0.245706
epoch 254, loss 0.245444
epoch 255, loss 0.245266
epoch 257, loss 0.245262
epoch 259, loss 0.244920
epoch 260, loss 0.244715
epoch 261, loss 0.244606
epoch 262, loss 0.244326
epoch 263, loss 0.244135
epoch 265, loss 0.243866
epoch 266, loss 0.243561
epoch 267, loss 0.243210
epoch 268, loss 0.243193
epoch 272, loss 0.243003
epoch 273, loss 0.242601
epoch 274, loss 0.242559
epoch 280, loss 0.242159
epoch 281, loss 0.242080
epoch 282, loss 0.241719
epoch 283, loss 0.241229
epoch 284, loss 0.240992
epoch 287, loss 0.240913


epoch 239, loss 0.235549
epoch 240, loss 0.235415
epoch 243, loss 0.235298
epoch 246, loss 0.235282
epoch 249, loss 0.235218
epoch 250, loss 0.235103
epoch 251, loss 0.234602
epoch 253, loss 0.234595
epoch 254, loss 0.234507
epoch 255, loss 0.234169
epoch 259, loss 0.233969
epoch 260, loss 0.233710
epoch 263, loss 0.233596
epoch 264, loss 0.233428
epoch 265, loss 0.233404
epoch 268, loss 0.233367
epoch 269, loss 0.233116
epoch 270, loss 0.233052
epoch 275, loss 0.232985
epoch 276, loss 0.232875
epoch 279, loss 0.232561
epoch 281, loss 0.232358
epoch 283, loss 0.232158
epoch 284, loss 0.231929
epoch 285, loss 0.231760
epoch 291, loss 0.231210
epoch 299, loss 0.231098
epoch 302, loss 0.231091
epoch 303, loss 0.230871
epoch 305, loss 0.230794
epoch 308, loss 0.230686
epoch 309, loss 0.230481
epoch 310, loss 0.230105
epoch 313, loss 0.230016
epoch 315, loss 0.229946
epoch 320, loss 0.229785
epoch 323, loss 0.229345
epoch 324, loss 0.229175
epoch 325, loss 0.228738
epoch 336, loss 0.228536


In [ ]:
#####################

In [ ]:
config_l2 = {
    'n_epochs': 1000,                # maximum number of epochs
    'batch_size': 98,                # mini-batch size for dataloader
    'optimizer': 'SGD',              # optimization algorithm (optimizer in torch.optim)
    'optim_hparas': {                # hyper-parameters for the optimizer (depends on which optimizer you are using)
        'lr': 0.001,                 # learning rate of SGD
        'momentum': 0.8              # momentum for SGD
    },
    'early_stop': 200,               # early stopping epochs (the number epochs since your model's last improvement)
    'save_path': 'models/model.pth', # your model will be saved here
    'L1_w': 0,                       # weight of L1 term
    'alpha': .001                    # weight of regularizaition terms
}

In [ ]:
train_data_l2 = data_loader(df, 'train', config_l2['batch_size'])
test_data_l2 = data_loader(df, 'test', config_l2['batch_size'])

In [ ]:
model_l2 = NeuralNet(train_data_l2.dataset.dim) # Construct model and move to device
model_loss_l2, model_loss_record_l2 = train(train_data_l2, test_data_l2, model_l2, config_l2, device)

In [ ]:
plot_learning_curve(model_loss_record_l2, title='Ridge')

## 1.4 MLP with Elastic Net regularization

In [ ]:
config_en = {
    'n_epochs': 1000,                 # maximum number of epochs
    'batch_size': 98,                 # mini-batch size for dataloader
    'optimizer': 'SGD',               # optimization algorithm (optimizer in torch.optim)
    'optim_hparas': {                 # hyper-parameters for the optimizer (depends on which optimizer you are using)
        'lr': 0.001,                  # learning rate of SGD
        'momentum': 0.8               # momentum for SGD
    },
    'early_stop': 200,                # early stopping epochs (the number epochs since your model's last improvement)
    'save_path': 'models/model.pth',  # your model will be saved here
    'L1_w': 0.5,                      # weight of L1 term
    'alpha': .001                     # weight of regularizaition terms
}

In [20]:

config_random_en = {
    'n_epochs': 1000,                # maximum number of epochs
    'batch_size': 98,                # mini-batch size for dataloader
    'optimizer': 'SGD',              # optimization algorithm (optimizer in torch.optim)
    'optim_hparas': {                # hyper-parameters for the optimizer (depends on which optimizer you are using)
        'lr': 0.001,                 # learning rate of SGD
        'momentum': 0.8              # momentum for SGD
    },
    'early_stop': 200,               # early stopping epochs (the number epochs since your model's last improvement)
    'save_path': 'models/model.pth', # your model will be saved here
    'L1_w': [i/10 for i in range(1,10)],      # weight of L1 term
    'alpha': [1, .1, .3, .5, .7, .9, .01, .03, .05, .07, .09, .001, .003, .005, .007, .009, .0001, .0003, .0005, .0007, .0009]  # weight of regularizaition terms
}

def random_search_en(iteration, config_random):
    print('test')
    iteration = iteration
    min_loss = 1000
    config_best = None
    
    config_record = []
    for i in range(iteration):
        config_candidate = config_random.copy()
        L1_w_index = randint(0,len(config_candidate['L1_w'])-1)
        alpha_index = randint(0,len(config_candidate['alpha'])-1)
        
        if (L1_w_index, alpha_index) in config_record:  # if a config has been tested then skip it
            continue
        
        config_record.append((L1_w_index, alpha_index))
        
        loss_record_5_fold = []
        
        config_candidate['L1_w'] = config_candidate['L1_w'][L1_w_index]
        config_candidate['alpha'] = config_candidate['alpha'][alpha_index]
        
        # 5 fold validation
        for j in range(5):
            train_data_en = data_loader(df, 'train', 98, random_state=j)
            test_data_en = data_loader(df, 'test', 98, random_state=j)
            model_en = NeuralNet(train_data_en.dataset.dim)

            model_loss_en, model_loss_record_en = train(train_data_en, test_data_en, model_en, config_candidate, device)
            
            loss_record_5_fold.append(model_loss_en)
        
        mean_loss = np.mean(loss_record_5_fold)
        
        if mean_loss < min_loss:
            min_loss = mean_loss
            config_best = config_candidate
    print('The lowest loss is {}\nConfig is {}'.format(min_loss, config_best))

time_start = time.time()
random_search_en(100, config_random_en)
time_end = time.time()
print('Total Time: ', time_end-time_start)

test
Finish reading the train data. 390samples and dim = 13
Finish reading the test data. 98samples and dim = 13
epoch 1, loss 1.875173
epoch 2, loss 1.684792
epoch 3, loss 1.524658
epoch 4, loss 1.402962
epoch 5, loss 1.320579
epoch 6, loss 1.263060
epoch 7, loss 1.224694
epoch 8, loss 1.198604
epoch 9, loss 1.180328
epoch 10, loss 1.166802
epoch 11, loss 1.155859
epoch 12, loss 1.146772
epoch 13, loss 1.139130
epoch 14, loss 1.132294
epoch 15, loss 1.126637
epoch 16, loss 1.121005
epoch 17, loss 1.116130
epoch 18, loss 1.111346
epoch 19, loss 1.107045
epoch 20, loss 1.103034
epoch 21, loss 1.099345
epoch 22, loss 1.096098
epoch 23, loss 1.093036
epoch 24, loss 1.089931
epoch 25, loss 1.087150
epoch 26, loss 1.084768
epoch 27, loss 1.082220
epoch 28, loss 1.079817
epoch 29, loss 1.077530
epoch 30, loss 1.075526
epoch 31, loss 1.073460
epoch 32, loss 1.071495
epoch 33, loss 1.069666
epoch 34, loss 1.068017
epoch 35, loss 1.066250
epoch 36, loss 1.064396
epoch 37, loss 1.062998
epoch 38

epoch 334, loss 0.858353
epoch 335, loss 0.857754
epoch 336, loss 0.857274
epoch 337, loss 0.856726
epoch 338, loss 0.855969
epoch 339, loss 0.855429
epoch 340, loss 0.854924
epoch 341, loss 0.854173
epoch 342, loss 0.853676
epoch 343, loss 0.853110
epoch 344, loss 0.852491
epoch 345, loss 0.851862
epoch 346, loss 0.851254
epoch 347, loss 0.850686
epoch 348, loss 0.850261
epoch 349, loss 0.849829
epoch 350, loss 0.849082
epoch 351, loss 0.848546
epoch 352, loss 0.848008
epoch 353, loss 0.847447
epoch 354, loss 0.846786
epoch 355, loss 0.846142
epoch 356, loss 0.845609
epoch 357, loss 0.845118
epoch 358, loss 0.844658
epoch 359, loss 0.843997
epoch 360, loss 0.843369
epoch 361, loss 0.842795
epoch 362, loss 0.842250
epoch 363, loss 0.841583
epoch 364, loss 0.841084
epoch 365, loss 0.840402
epoch 366, loss 0.839763
epoch 367, loss 0.839193
epoch 368, loss 0.838683
epoch 369, loss 0.838087
epoch 370, loss 0.837615
epoch 371, loss 0.836993
epoch 372, loss 0.836407
epoch 373, loss 0.835825


epoch 663, loss 0.682290
epoch 664, loss 0.681840
epoch 665, loss 0.681223
epoch 666, loss 0.680974
epoch 667, loss 0.680399
epoch 668, loss 0.679885
epoch 669, loss 0.679328
epoch 670, loss 0.678890
epoch 671, loss 0.678249
epoch 672, loss 0.677857
epoch 673, loss 0.677407
epoch 674, loss 0.676839
epoch 675, loss 0.676480
epoch 676, loss 0.675885
epoch 677, loss 0.675451
epoch 678, loss 0.674832
epoch 679, loss 0.674338
epoch 680, loss 0.673794
epoch 681, loss 0.673452
epoch 682, loss 0.673031
epoch 683, loss 0.672322
epoch 684, loss 0.672015
epoch 685, loss 0.671446
epoch 686, loss 0.670975
epoch 687, loss 0.670474
epoch 688, loss 0.669894
epoch 689, loss 0.669487
epoch 690, loss 0.668868
epoch 691, loss 0.668461
epoch 692, loss 0.667980
epoch 693, loss 0.667417
epoch 694, loss 0.667035
epoch 695, loss 0.666540
epoch 696, loss 0.666122
epoch 697, loss 0.665580
epoch 698, loss 0.665102
epoch 699, loss 0.664537
epoch 700, loss 0.664026
epoch 701, loss 0.663495
epoch 702, loss 0.662997


epoch 993, loss 0.532093
epoch 994, loss 0.531593
epoch 995, loss 0.531183
epoch 996, loss 0.530824
epoch 997, loss 0.530458
epoch 998, loss 0.530029
epoch 999, loss 0.529593
epoch 1000, loss 0.529104
Final loss is 0.529104 after 1000 epochs
Finish reading the train data. 390samples and dim = 13
Finish reading the test data. 98samples and dim = 13
epoch 1, loss 1.860927
epoch 2, loss 1.694922
epoch 3, loss 1.548372
epoch 4, loss 1.439560
epoch 5, loss 1.368940
epoch 6, loss 1.324428
epoch 7, loss 1.292361
epoch 8, loss 1.272338
epoch 9, loss 1.255879
epoch 10, loss 1.244552
epoch 11, loss 1.234721
epoch 12, loss 1.225936
epoch 13, loss 1.219187
epoch 14, loss 1.213520
epoch 15, loss 1.208462
epoch 16, loss 1.203518
epoch 17, loss 1.198448
epoch 18, loss 1.193971
epoch 19, loss 1.190483
epoch 20, loss 1.187172
epoch 21, loss 1.183462
epoch 22, loss 1.179947
epoch 23, loss 1.177052
epoch 24, loss 1.173730
epoch 25, loss 1.171391
epoch 26, loss 1.168524
epoch 27, loss 1.166345
epoch 28, l

epoch 333, loss 0.946790
epoch 334, loss 0.945949
epoch 335, loss 0.945191
epoch 336, loss 0.945125
epoch 337, loss 0.944453
epoch 338, loss 0.943751
epoch 339, loss 0.942878
epoch 340, loss 0.942588
epoch 341, loss 0.942535
epoch 342, loss 0.941516
epoch 343, loss 0.940643
epoch 345, loss 0.939741
epoch 346, loss 0.939242
epoch 347, loss 0.938836
epoch 348, loss 0.938049
epoch 349, loss 0.937262
epoch 350, loss 0.936701
epoch 351, loss 0.936071
epoch 352, loss 0.935651
epoch 353, loss 0.935297
epoch 354, loss 0.933980
epoch 355, loss 0.933320
epoch 356, loss 0.932844
epoch 357, loss 0.932789
epoch 358, loss 0.932334
epoch 359, loss 0.931991
epoch 360, loss 0.930979
epoch 361, loss 0.930716
epoch 362, loss 0.930042
epoch 363, loss 0.929230
epoch 364, loss 0.928417
epoch 365, loss 0.928303
epoch 366, loss 0.927363
epoch 367, loss 0.926888
epoch 368, loss 0.926513
epoch 369, loss 0.925582
epoch 370, loss 0.924731
epoch 371, loss 0.924707
epoch 372, loss 0.923815
epoch 373, loss 0.923098


...

epoch 455, loss 0.188152
epoch 459, loss 0.187924
epoch 461, loss 0.187885
epoch 464, loss 0.187764
epoch 467, loss 0.187686
epoch 476, loss 0.187437
epoch 480, loss 0.187415
epoch 493, loss 0.187220
epoch 499, loss 0.187196
epoch 500, loss 0.187183
epoch 501, loss 0.187059
epoch 507, loss 0.186966
epoch 511, loss 0.186912
epoch 512, loss 0.186730
epoch 521, loss 0.186677
epoch 528, loss 0.186661
epoch 532, loss 0.186574
epoch 541, loss 0.186334
epoch 559, loss 0.186022
epoch 564, loss 0.185917
epoch 576, loss 0.185764
epoch 577, loss 0.185690
epoch 603, loss 0.185455
Final loss is 0.185455 after 804 epochs
Finish reading the train data. 390samples and dim = 13
Finish reading the test data. 98samples and dim = 13
epoch 1, loss 0.989852
epoch 2, loss 0.804163
epoch 3, loss 0.660110
epoch 4, loss 0.569502
epoch 5, loss 0.518192
epoch 6, loss 0.485194
epoch 7, loss 0.463130
epoch 8, loss 0.446494
epoch 9, loss 0.432872
epoch 10, loss 0.421735
epoch 11, loss 0.411002
epoch 12, loss 0.40128

epoch 33, loss 1.974891
epoch 36, loss 1.973698
epoch 39, loss 1.973101
epoch 41, loss 1.965832
Final loss is 1.965832 after 242 epochs
Finish reading the train data. 390samples and dim = 13
Finish reading the test data. 98samples and dim = 13
epoch 1, loss 162.239410
epoch 2, loss 146.036575
epoch 3, loss 128.059967
epoch 4, loss 110.546646
epoch 5, loss 93.822647
epoch 6, loss 78.449944
epoch 7, loss 64.403419
epoch 8, loss 51.754654
epoch 9, loss 40.601555
epoch 10, loss 30.900587
epoch 11, loss 22.817282
epoch 12, loss 16.045876
epoch 13, loss 10.638129
epoch 14, loss 6.531333
epoch 15, loss 4.112577
epoch 16, loss 2.942585
epoch 17, loss 2.704854
epoch 18, loss 2.358192
epoch 19, loss 2.309925
epoch 20, loss 2.186655
epoch 21, loss 2.183781
epoch 23, loss 2.169176
epoch 24, loss 2.162850
epoch 26, loss 2.150872
epoch 30, loss 2.143289
epoch 32, loss 2.141518
epoch 35, loss 2.133260
epoch 42, loss 2.128841
Final loss is 2.128841 after 243 epochs
Finish reading the train data. 390sa

epoch 72, loss 1.271081
epoch 73, loss 1.264098
epoch 74, loss 1.258990
epoch 75, loss 1.255280
epoch 76, loss 1.247972
epoch 77, loss 1.243943
epoch 78, loss 1.241841
epoch 79, loss 1.236487
epoch 80, loss 1.231228
epoch 81, loss 1.227844
epoch 82, loss 1.221387
epoch 83, loss 1.213565
epoch 84, loss 1.210607
epoch 85, loss 1.204016
epoch 86, loss 1.196679
epoch 87, loss 1.194391
epoch 88, loss 1.184466
epoch 89, loss 1.176998
epoch 90, loss 1.172827
epoch 91, loss 1.163825
epoch 92, loss 1.157305
epoch 93, loss 1.151218
epoch 94, loss 1.143129
epoch 95, loss 1.134113
epoch 96, loss 1.127658
epoch 97, loss 1.118693
epoch 98, loss 1.112022
epoch 99, loss 1.109371
epoch 100, loss 1.101120
epoch 101, loss 1.094526
epoch 102, loss 1.092091
epoch 103, loss 1.083920
epoch 104, loss 1.078238
epoch 105, loss 1.075464
epoch 106, loss 1.069344
epoch 107, loss 1.064368
epoch 108, loss 1.062306
epoch 109, loss 1.055840
epoch 110, loss 1.048876
epoch 111, loss 1.044174
epoch 112, loss 1.039471
epo

epoch 223, loss 0.889341
epoch 228, loss 0.888494
epoch 231, loss 0.887906
epoch 237, loss 0.886925
epoch 240, loss 0.885948
epoch 246, loss 0.885779
epoch 249, loss 0.885514
epoch 255, loss 0.884408
epoch 258, loss 0.883613
epoch 261, loss 0.883601
epoch 267, loss 0.882760
epoch 273, loss 0.882701
epoch 276, loss 0.882508
epoch 281, loss 0.882442
epoch 283, loss 0.882120
epoch 285, loss 0.881936
epoch 286, loss 0.881842
epoch 291, loss 0.881649
epoch 293, loss 0.881063
epoch 300, loss 0.879702
epoch 303, loss 0.879350
epoch 318, loss 0.878815
epoch 330, loss 0.878166
epoch 339, loss 0.877997
epoch 345, loss 0.877481
epoch 358, loss 0.877423
epoch 363, loss 0.876369
epoch 384, loss 0.876342
epoch 393, loss 0.875135
epoch 408, loss 0.874803
epoch 429, loss 0.874428
epoch 453, loss 0.874210
epoch 462, loss 0.874118
epoch 483, loss 0.872821
epoch 528, loss 0.872529
epoch 555, loss 0.872446
epoch 573, loss 0.872099
epoch 618, loss 0.871804
epoch 633, loss 0.871762
epoch 663, loss 0.871272


epoch 38, loss 7.779293
epoch 39, loss 7.258124
epoch 40, loss 6.762954
epoch 41, loss 6.296919
epoch 42, loss 5.850813
epoch 43, loss 5.423838
epoch 44, loss 5.020553
epoch 45, loss 4.647470
epoch 46, loss 4.297541
epoch 47, loss 3.968433
epoch 48, loss 3.657612
epoch 49, loss 3.369384
epoch 50, loss 3.102724
epoch 51, loss 2.843113
epoch 52, loss 2.603305
epoch 53, loss 2.383937
epoch 54, loss 2.186023
epoch 55, loss 2.004119
epoch 56, loss 1.838044
epoch 57, loss 1.694261
epoch 58, loss 1.572937
epoch 59, loss 1.465911
epoch 60, loss 1.382011
epoch 61, loss 1.315671
epoch 62, loss 1.274467
epoch 63, loss 1.250159
epoch 64, loss 1.228554
epoch 65, loss 1.209749
epoch 66, loss 1.197299
epoch 67, loss 1.183164
epoch 68, loss 1.168480
epoch 69, loss 1.155510
epoch 70, loss 1.142411
epoch 71, loss 1.129019
epoch 72, loss 1.119261
epoch 73, loss 1.106957
epoch 74, loss 1.098022
epoch 75, loss 1.090387
epoch 76, loss 1.080864
epoch 77, loss 1.072968
epoch 78, loss 1.064633
epoch 79, loss 1

## 1.5 MLP with tuning more possible hyperparameters


In [ ]:

config_random_more = {
    'n_epochs': 1000,                # maximum number of epochs
    'batch_size': [i for i in range(20, 100)],                # mini-batch size for dataloader
    'optimizer': 'SGD',              # optimization algorithm (optimizer in torch.optim)
    'optim_hparas': {                # hyper-parameters for the optimizer (depends on which optimizer you are using)
        'lr': 0.001,                 # learning rate of SGD
        'momentum': 0.8              # momentum for SGD
    },
    'early_stop': 200,               # early stopping epochs (the number epochs since your model's last improvement)
    'save_path': 'models/model.pth', # your model will be saved here
    'L1_w': [i/10 for i in range(1,10)],      # weight of L1 term
    'alpha': [10, 1, .1, .01, .001, .0001]  # weight of regularizaition terms
}

def random_search_en(iteration, config_random):
    print('test')
    iteration = iteration
    min_loss = 1000
    config_best = None
    
    config_record = []
    for i in range(iteration):
        config_candidate = config_random.copy()
        L1_w_index = randint(0,len(config_candidate['L1_w'])-1)
        alpha_index = randint(0,len(config_candidate['alpha'])-1)
        
        if (L1_w_index, alpha_index) in config_record:  # if a config has been tested then skip it
            continue
        
        config_record.append((L1_w_index, alpha_index))
        
        loss_record_5_fold = []
        
        config_candidate['L1_w'] = config_candidate['L1_w'][L1_w_index]
        config_candidate['alpha'] = config_candidate['alpha'][alpha_index]
        
        # 5 fold validation
        for j in range(5):
            train_data_en = data_loader(df, 'train', 98, random_state=j)
            test_data_en = data_loader(df, 'test', 98, random_state=j)
            model_en = NeuralNet(train_data_en.dataset.dim)

            model_loss_en, model_loss_record_en = train(train_data_en, test_data_en, model_en, config_candidate, device)
            
            loss_record_5_fold.append(model_loss_en)
        
        mean_loss = np.mean(loss_record_5_fold)
        
        if mean_loss < min_loss:
            min_loss = mean_loss
            config_best = config_candidate
    print('The lowest loss is {}\nConfig is {}'.format(min_loss, config_best))

time_start = time.time()
random_search_en(100, config_random_en)
time_end = time.time()
print('Total Time: %s', time_end-time_start)

In [ ]:
df_try = pd.read_csv('Boston.csv')
df_try.head(10)

In [ ]:
from sklearn.preprocessing import StandardScaler, MinMaxScaler, RobustScaler

scalar = StandardScaler()

df_try = scalar.fit_transform(df_try)
print(df_try)

In [23]:
for i in range(10):
    print('iteration ', i)
    if i == 5:
        continue
    print('end of this iteration ', i)
    print('end')

iteration  0
end of this iteration  0
end
iteration  1
end of this iteration  1
end
iteration  2
end of this iteration  2
end
iteration  3
end of this iteration  3
end
iteration  4
end of this iteration  4
end
iteration  5
iteration  6
end of this iteration  6
end
iteration  7
end of this iteration  7
end
iteration  8
end of this iteration  8
end
iteration  9
end of this iteration  9
end
